In [1]:
import torch
import numpy as np
from collections import defaultdict

import pandas as pd
import pathlib
from rich import print

import matplotlib.pyplot as plt

# set pyplot theme to ggplot2
plt.style.use("ggplot")
import wandb

In [2]:
source_csv_filepath = (
    "13032024-full.csv"
)
source_csv_filepath = pathlib.Path(source_csv_filepath)

In [3]:
def load_data_as_df(filepath):
    df = pd.read_csv(filepath)

    # Concatenating the header with the first row
    new_headers = [f"{col.split('.')[0]}.{df.iloc[0][idx]}" for idx, col in enumerate(df.columns)]

    # Setting the new concatenated values as column names
    df.columns = new_headers

    # Removing the first row from the DataFrame
    df = df.drop(df.index[0])

    # Resetting the DataFrame index
    df.reset_index(drop=True, inplace=True)
    # replace NA with 5
    df = df.fillna(5)
    return df

In [4]:
df = load_data_as_df(source_csv_filepath)

# visualize using tabulate for ipython noteboooks
from IPython.display import display

# Assuming df is your DataFrame
with pd.option_context("display.max_rows", None, "display.max_columns", None):
    display(
        df.style.set_table_attributes('style="display:inline"').bar(
            color="lightblue"
        )
    )

/var/folders/gh/_5t3nhn94t12m7rh483b8b7r0000gn/T/ipykernel_41281/2468503343.py:5: FutureWarning: Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `ser.iloc[pos]`
  new_headers = [f"{col.split('.')[0]}.{df.iloc[0][idx]}" for idx, col in enumerate(df.columns)]


In [5]:
import plotly.express as px

# List of all columns (replace with your actual column names)
# df = pd.read_csv(source_csv_filepath)
df = load_data_as_df(source_csv_filepath)
columns = df.columns.tolist()[1:]
model_names = df.columns.tolist()[0]
# remove all datapoints with less than 50% on imagenet1k.1


# model_names = df[model_names][1:]

# Convert all columns (except the first) to numeric
for col in df.columns[1:]:
    df[col] = pd.to_numeric(df[col], errors="coerce")

# df = df[df["imagenet1k.acc@1"] > 50]
# Set the first column as index (to be used as labels)
# df.set_index(df.columns[0], inplace=True)
for idx, col in enumerate(columns):  # Exclude first column from plotting
    fig = px.scatter(
        df,
        x="imagenet1k.acc@1",
        y=col,
        title=f"Scatter plot of {col} vs imagenet1k acc@1",
    )
    fig.update_traces(
        mode="markers+text",
        marker=dict(size=5),
        text=df[model_names],
        textposition="top center",
        textfont=dict(size=8),
    )  # Adjust marker size and add labels here
    fig.show()

/var/folders/gh/_5t3nhn94t12m7rh483b8b7r0000gn/T/ipykernel_41281/2468503343.py:5: FutureWarning: Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `ser.iloc[pos]`
  new_headers = [f"{col.split('.')[0]}.{df.iloc[0][idx]}" for idx, col in enumerate(df.columns)]


In [6]:
# Convert all columns (except the first) to numeric
df = load_data_as_df(source_csv_filepath)
columns = df.columns.tolist()[1:]
model_names = df.columns.tolist()[0]

for col in df.columns[1:]:
    df[col] = pd.to_numeric(df[col], errors="coerce")
    # normalize the data
    # df[col] = (df[col] - df[col].mean()) / df[col].std()

# Set the first column as index (to be used as labels)
df.set_index(df.columns[0], inplace=True)

correlation_matrix = df.corr(method="spearman")["imagenet1k.acc@1"]
print(correlation_matrix)

sorted_correlation_matrix = correlation_matrix.abs().sort_values(
    ascending=False
)
print(sorted_correlation_matrix)

# return as latex table
print(sorted_correlation_matrix.to_latex())

/var/folders/gh/_5t3nhn94t12m7rh483b8b7r0000gn/T/ipykernel_41281/2468503343.py:5: FutureWarning:

Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `ser.iloc[pos]`



cityscapes.mIoU                                0.758539
cityscapes.dice-loss                          -0.701571
acdc.dice-loss                                -0.515464
ade20k.mIoU                                    0.800000
ade20k.dice-loss                               0.400294
aircraft.acc@1                                 0.817647
chexpert.auc                                   0.657334
cifar100.loss                                 -0.861765
cifar100.acc@5                                 0.864706
cifar100.acc@1                                 0.847059
clevr.acc@1                                    0.555882
clevr-math.acc@5                               0.664706
clevr-math.acc@1                               0.732353
coco-10k.mIoU                                  0.807070
coco-10k.dice-loss                            -0.191458
coco-164k.mIoU                                 0.779412
coco-164k.dice-loss                           -0.389993
cubirds.acc@1                                  0.823529
diabetic.auc                                   0.815306
dtextures.acc@1                                0.699044
flickr30k.text-to-image-acc@5                  0.817379
flickr30k.text-to-image-acc@1                  0.813290
flickr30k.image-to-text-acc@1                  0.804718
flickr30k.image-to-text-acc@5                  0.822664
food101.loss                                  -0.847059
food101.acc@5                                  0.820588
food101.acc@1                                  0.832353
fungi.acc@1                                    0.779985
ham10k.auc                                     0.713030
hmdb51.acc@5                                   0.824136
hmdb51.acc@1                                   0.846611
imagenet1k.loss                               -0.991176
imagenet1k.acc@5                               0.973529
imagenet1k.acc@1                               1.000000
iwildcam.mae                                  -0.705882
kinetics.acc@5                                 0.837381
kinetics.acc@1                                 0.850000
mini.acc@1                                     0.852097
newyorkercaptioncontest.text-to-image-acc@5    0.820588
newyorkercaptioncontest.text-to-image-acc@1    0.798234
newyorkercaptioncontest.image-to-text-acc@1    0.774011
newyorkercaptioncontest.image-to-text-acc@5    0.791176
nyu.mIoU                                       0.255882
nyu.dice-loss                                  0.277082
omniglot.acc@1                                 0.652800
pascal.mIoU                                    0.902941
pascal.dice-loss                               0.261765
places365.loss                                -0.855882
places365.acc@5                                0.838235
places365.acc@1                                0.841176
pokemonblipcaptions.text-to-image-acc@5        0.514706
pokemonblipcaptions.text-to-image-acc@1        0.467647
pokemonblipcaptions.image-to-text-acc@1        0.508824
pokemonblipcaptions.image-to-text-acc@5        0.511765
ucf.acc@5                                      0.835909
ucf.acc@1                                      0.844118
vgg.acc@1                                      0.799117
winoground.text-to-image-acc@1                -0.004415
winoground.image-to-text-acc@1                -0.134021
Name: imagenet1k.acc@1, dtype: float64

imagenet1k.acc@1                               1.000000
imagenet1k.loss                                0.991176
imagenet1k.acc@5                               0.973529
pascal.mIoU                                    0.902941
cifar100.acc@5                                 0.864706
cifar100.loss                                  0.861765
places365.loss                                 0.855882
mini.acc@1                                     0.852097
kinetics.acc@1                                 0.850000
cifar100.acc@1                                 0.847059
food101.loss                                   0.847059
hmdb51.acc@1                                   0.846611
ucf.acc@1                                      0.844118
places365.acc@1                                0.841176
places365.acc@5                                0.838235
kinetics.acc@5                                 0.837381
ucf.acc@5                                      0.835909
food101.acc@1                                  0.832353
hmdb51.acc@5                                   0.824136
cubirds.acc@1                                  0.823529
flickr30k.image-to-text-acc@5                  0.822664
food101.acc@5                                  0.820588
newyorkercaptioncontest.text-to-image-acc@5    0.820588
aircraft.acc@1                                 0.817647
flickr30k.text-to-image-acc@5                  0.817379
diabetic.auc                                   0.815306
flickr30k.text-to-image-acc@1                  0.813290
coco-10k.mIoU                                  0.807070
flickr30k.image-to-text-acc@1                  0.804718
ade20k.mIoU                                    0.800000
vgg.acc@1                                      0.799117
newyorkercaptioncontest.text-to-image-acc@1    0.798234
newyorkercaptioncontest.image-to-text-acc@5    0.791176
fungi.acc@1                                    0.779985
coco-164k.mIoU                                 0.779412
newyorkercaptioncontest.image-to-text-acc@1    0.774011
cityscapes.mIoU                                0.758539
clevr-math.acc@1                               0.732353
ham10k.auc                                     0.713030
iwildcam.mae                                   0.705882
cityscapes.dice-loss                           0.701571
dtextures.acc@1                                0.699044
clevr-math.acc@5                               0.664706
chexpert.auc                                   0.657334
omniglot.acc@1                                 0.652800
clevr.acc@1                                    0.555882
acdc.dice-loss                                 0.515464
pokemonblipcaptions.text-to-image-acc@5        0.514706
pokemonblipcaptions.image-to-text-acc@5        0.511765
pokemonblipcaptions.image-to-text-acc@1        0.508824
pokemonblipcaptions.text-to-image-acc@1        0.467647
ade20k.dice-loss                               0.400294
coco-164k.dice-loss                            0.389993
nyu.dice-loss                                  0.277082
pascal.dice-loss                               0.261765
nyu.mIoU                                       0.255882
coco-10k.dice-loss                             0.191458
winoground.image-to-text-acc@1                 0.134021
winoground.text-to-image-acc@1                 0.004415
Name: imagenet1k.acc@1, dtype: float64

\begin{tabular}{lr}
\toprule
 & imagenet1k.acc@1 \\
\midrule
imagenet1k.acc@1 & 1.000000 \\
imagenet1k.loss & 0.991176 \\
imagenet1k.acc@5 & 0.973529 \\
pascal.mIoU & 0.902941 \\
cifar100.acc@5 & 0.864706 \\
cifar100.loss & 0.861765 \\
places365.loss & 0.855882 \\
mini.acc@1 & 0.852097 \\
kinetics.acc@1 & 0.850000 \\
cifar100.acc@1 & 0.847059 \\
food101.loss & 0.847059 \\
hmdb51.acc@1 & 0.846611 \\
ucf.acc@1 & 0.844118 \\
places365.acc@1 & 0.841176 \\
places365.acc@5 & 0.838235 \\
kinetics.acc@5 & 0.837381 \\
ucf.acc@5 & 0.835909 \\
food101.acc@1 & 0.832353 \\
hmdb51.acc@5 & 0.824136 \\
cubirds.acc@1 & 0.823529 \\
flickr30k.image-to-text-acc@5 & 0.822664 \\
food101.acc@5 & 0.820588 \\
newyorkercaptioncontest.text-to-image-acc@5 & 0.820588 \\
aircraft.acc@1 & 0.817647 \\
flickr30k.text-to-image-acc@5 & 0.817379 \\
diabetic.auc & 0.815306 \\
flickr30k.text-to-image-acc@1 & 0.813290 \\
coco-10k.mIoU & 0.807070 \\
flickr30k.image-to-text-acc@1 & 0.804718 \\
ade20k.mIoU & 0.800000 \\
vgg.acc@1 & 0.799117 \\
newyorkercaptioncontest.text-to-image-acc@1 & 0.798234 \\
newyorkercaptioncontest.image-to-text-acc@5 & 0.791176 \\
fungi.acc@1 & 0.779985 \\
coco-164k.mIoU & 0.779412 \\
newyorkercaptioncontest.image-to-text-acc@1 & 0.774011 \\
cityscapes.mIoU & 0.758539 \\
clevr-math.acc@1 & 0.732353 \\
ham10k.auc & 0.713030 \\
iwildcam.mae & 0.705882 \\
cityscapes.dice-loss & 0.701571 \\
dtextures.acc@1 & 0.699044 \\
clevr-math.acc@5 & 0.664706 \\
chexpert.auc & 0.657334 \\
omniglot.acc@1 & 0.652800 \\
clevr.acc@1 & 0.555882 \\
acdc.dice-loss & 0.515464 \\
pokemonblipcaptions.text-to-image-acc@5 & 0.514706 \\
pokemonblipcaptions.image-to-text-acc@5 & 0.511765 \\
pokemonblipcaptions.image-to-text-acc@1 & 0.508824 \\
pokemonblipcaptions.text-to-image-acc@1 & 0.467647 \\
ade20k.dice-loss & 0.400294 \\
coco-164k.dice-loss & 0.389993 \\
nyu.dice-loss & 0.277082 \\
pascal.dice-loss & 0.261765 \\
nyu.mIoU & 0.255882 \\
coco-10k.dice-loss & 0.191458 \\
winoground.image-to-text-acc@1 & 0.134021 \\
winoground.text-to-image-acc@1 & 0.004415 \\
\bottomrule
\end{tabular}

Just threshold at 60% for imagenet (top 1), recompute the above so we get some signal towards the question "If A does better than B, where both A and B do 'well' on imagenet, do I have a reason to believe that A IS better than B on previously unseen scenarios. Use spearman correlation. For how many times A is Better than B, count how many times it happens and compute a probability.

In [7]:
from sklearn.linear_model import LinearRegression
from sklearn.model_selection import KFold
from sklearn.metrics import root_mean_squared_error

# Assuming df is your DataFrame
X = df.copy()
X.dropna(inplace=True)
# Create a linear regression model


# Use leave-one-out cross-validation
kfold = KFold(n_splits=10)

# Dictionary to store the average RMSE for each metric
avg_rmse_dict = {}
std_rmse_dict = {}
# 47 x 16

# train: 47 x 8 -> x = 1 x 8, y = 46 x 8
# test: 47 x 8 -> x = 1 x 8, y = 46 x 8

# For each column in the DataFrame
for col in df.columns:
    # Use the column as the input and the remaining columns as the target
    x = X[[col]]
    y = X

    # Initialize a list to store the RMSE for each target column
    rmse_scores = []

    # For each row (leave-one-out cross-validation)
    for train_index, test_index in kfold.split(x):
        model = LinearRegression()
        # Split the data into training and testing sets
        x_train, x_test = x.iloc[train_index], x.iloc[test_index]
        y_train, y_test = y.iloc[train_index], y.iloc[test_index]

        # Fit the model
        model.fit(x_train, y_train)

        # Make predictions
        y_pred = model.predict(x_test)

        # Calculate the RMSE and add it to the list
        rmse_scores.append(root_mean_squared_error(y_test, y_pred))

    # Calculate the average RMSE
    avg_rmse = np.mean(rmse_scores)
    std_rmse = np.std(rmse_scores)

    # Store the average RMSE in the dictionary
    avg_rmse_dict[col] = avg_rmse
    std_rmse_dict[col] = std_rmse

# Find the metric with the lowest RMSE
best_metric = min(avg_rmse_dict, key=avg_rmse_dict.get)

print(
    f"The most predictive metric is {best_metric} with an average RMSE of {avg_rmse_dict[best_metric]}"
)
# print(f'-- Mean RMSE --')
# print(avg_rmse_dict)
# print(f'-- Std RMSE --')
# print(std_rmse_dict)

# sort by value
sorted_avg_rmse_dict = sorted(avg_rmse_dict.items(), key=lambda x: x[1])
sorted_std_rmse_dict = sorted(std_rmse_dict.items(), key=lambda x: x[1])

print(f"-- Mean RMSE Sorted --")
print(sorted_avg_rmse_dict)
print(f"-- Std RMSE Sorted --")
print(sorted_std_rmse_dict)

The most predictive metric is food101.acc@1 with an average RMSE of 2.862580963246862

-- Mean RMSE Sorted --

[
    ('food101.acc@1', 2.862580963246862),
    ('food101.loss', 2.9226155624487626),
    ('flickr30k.text-to-image-acc@5', 2.942876275293993),
    ('flickr30k.image-to-text-acc@5', 2.967737669017642),
    ('newyorkercaptioncontest.text-to-image-acc@5', 2.996591006570623),
    ('places365.acc@5', 3.033009612115051),
    ('newyorkercaptioncontest.image-to-text-acc@5', 3.0558715270344186),
    ('cifar100.loss', 3.0678274946172137),
    ('places365.acc@1', 3.1316549505435334),
    ('places365.loss', 3.162247571799534),
    ('newyorkercaptioncontest.text-to-image-acc@1', 3.1684340396042634),
    ('cifar100.acc@1', 3.1749797155214847),
    ('cityscapes.mIoU', 3.1835241585365717),
    ('coco-164k.mIoU', 3.2549490854583722),
    ('imagenet1k.loss', 3.2565117444741523),
    ('flickr30k.text-to-image-acc@1', 3.264741403505279),
    ('imagenet1k.acc@5', 3.268920467547236),
    ('dtextures.acc@1', 3.2717208395817403),
    ('food101.acc@5', 3.3128395707800897),
    ('diabetic.auc', 3.3266511512000596),
    ('cifar100.acc@5', 3.3636536478733596),
    ('coco-10k.mIoU', 3.368226605194464),
    ('fungi.acc@1', 3.3929401733080953),
    ('ucf.acc@5', 3.4550208200906156),
    ('cityscapes.dice-loss', 3.491235779439885),
    ('vgg.acc@1', 3.4960127421227156),
    ('flickr30k.image-to-text-acc@1', 3.5252772212397625),
    ('newyorkercaptioncontest.image-to-text-acc@1', 3.623911914741425),
    ('imagenet1k.acc@1', 3.6470188107550343),
    ('chexpert.auc', 3.6638925841545444),
    ('ucf.acc@1', 3.718634926017097),
    ('hmdb51.acc@5', 3.735412928141509),
    ('ade20k.mIoU', 3.7837048517299303),
    ('mini.acc@1', 3.7977587906659265),
    ('pascal.mIoU', 3.961691328080583),
    ('kinetics.acc@5', 4.002611067531341),
    ('cubirds.acc@1', 4.056386874734503),
    ('kinetics.acc@1', 4.222146701509927),
    ('hmdb51.acc@1', 4.235977528839024),
    ('ham10k.auc', 4.6335028619321985),
    ('aircraft.acc@1', 4.987575951938249),
    ('clevr-math.acc@1', 5.120332927280484),
    ('omniglot.acc@1', 5.229359505391568),
    ('clevr.acc@1', 6.050633808761843),
    ('acdc.dice-loss', 6.119391385097555),
    ('clevr-math.acc@5', 6.181688001854071),
    ('iwildcam.mae', 6.519945058916903),
    ('pokemonblipcaptions.image-to-text-acc@5', 7.795992432450008),
    ('nyu.dice-loss', 7.893604104740229),
    ('pokemonblipcaptions.text-to-image-acc@1', 8.024302357660693),
    ('pokemonblipcaptions.text-to-image-acc@5', 8.069053467282206),
    ('pokemonblipcaptions.image-to-text-acc@1', 8.140439430476349),
    ('winoground.text-to-image-acc@1', 8.489199894528875),
    ('nyu.mIoU', 8.536888843122972),
    ('winoground.image-to-text-acc@1', 8.784686885333473),
    ('pascal.dice-loss', 9.223477591783345),
    ('ade20k.dice-loss', 10.103095585726507),
    ('coco-164k.dice-loss', 11.035487121462381),
    ('coco-10k.dice-loss', 13.302373842314264)
]

-- Std RMSE Sorted --

[
    ('cifar100.acc@5', 1.1076238764285822),
    ('ade20k.mIoU', 1.1716014074633423),
    ('cifar100.loss', 1.1907291251878924),
    ('newyorkercaptioncontest.text-to-image-acc@5', 1.2303421260717267),
    ('pascal.mIoU', 1.2309805590627865),
    ('flickr30k.text-to-image-acc@1', 1.2323521725533766),
    ('cifar100.acc@1', 1.2397435656630311),
    ('newyorkercaptioncontest.image-to-text-acc@5', 1.2588659891018485),
    ('newyorkercaptioncontest.text-to-image-acc@1', 1.295140845360474),
    ('food101.acc@1', 1.3130408812307297),
    ('places365.loss', 1.3237985912069499),
    ('food101.loss', 1.327408946655647),
    ('newyorkercaptioncontest.image-to-text-acc@1', 1.3354000969992619),
    ('flickr30k.text-to-image-acc@5', 1.3361819626074007),
    ('places365.acc@5', 1.3418440441496566),
    ('coco-164k.mIoU', 1.3580191507062702),
    ('cityscapes.dice-loss', 1.3695765063165302),
    ('coco-10k.mIoU', 1.3792408755286851),
    ('dtextures.acc@1', 1.39248285651682),
    ('fungi.acc@1', 1.4050818254291906),
    ('cityscapes.mIoU', 1.4229581013784456),
    ('flickr30k.image-to-text-acc@5', 1.4254225714749555),
    ('food101.acc@5', 1.4303603096567523),
    ('flickr30k.image-to-text-acc@1', 1.4844132277514412),
    ('vgg.acc@1', 1.4848452024999048),
    ('ucf.acc@5', 1.5181695189395208),
    ('chexpert.auc', 1.5774347621360216),
    ('places365.acc@1', 1.6268170484380575),
    ('imagenet1k.acc@5', 1.6584492992512856),
    ('ucf.acc@1', 1.6925057845216833),
    ('diabetic.auc', 1.6980665853989672),
    ('cubirds.acc@1', 1.7120852128472224),
    ('imagenet1k.loss', 1.7271393423050412),
    ('hmdb51.acc@5', 1.751562537241057),
    ('mini.acc@1', 1.7958193303022176),
    ('hmdb51.acc@1', 1.862920894800236),
    ('clevr-math.acc@1', 2.0635547886836547),
    ('ham10k.auc', 2.0652796895511445),
    ('kinetics.acc@5', 2.112341030398236),
    ('kinetics.acc@1', 2.140881729730929),
    ('acdc.dice-loss', 2.1611886837957366),
    ('imagenet1k.acc@1', 2.231833507720336),
    ('omniglot.acc@1', 2.555733560607119),
    ('nyu.mIoU', 2.639670123749744),
    ('aircraft.acc@1', 2.722398793958356),
    ('winoground.image-to-text-acc@1', 2.7628628277928553),
    ('winoground.text-to-image-acc@1', 2.7658239654809),
    ('clevr-math.acc@5', 2.874964732290581),
    ('clevr.acc@1', 3.008450068140018),
    ('nyu.dice-loss', 3.2913670439632883),
    ('iwildcam.mae', 3.430282989567992),
    ('pokemonblipcaptions.text-to-image-acc@1', 3.4425430132815964),
    ('pokemonblipcaptions.text-to-image-acc@5', 3.6180372536571808),
    ('pokemonblipcaptions.image-to-text-acc@1', 3.6183757303769024),
    ('pokemonblipcaptions.image-to-text-acc@5', 3.7298316437047925),
    ('pascal.dice-loss', 5.607619473520834),
    ('ade20k.dice-loss', 6.664799142894983),
    ('coco-164k.dice-loss', 8.430233706126174),
    ('coco-10k.dice-loss', 15.137787514341216)
]

In [8]:
from itertools import combinations
from sklearn.linear_model import LinearRegression
from sklearn.model_selection import KFold
from sklearn.metrics import root_mean_squared_error

# Assuming df is your DataFrame
X = df.copy()
X.dropna(inplace=True)
# Create a linear regression model


# Use leave-one-out cross-validation
kfold = KFold(n_splits=10)

# Dictionary to store the average RMSE for each metric
avg_rmse_dict = {}
std_rmse_dict = {}
# 47 x 16
column_pairs = []

columns = df.columns.tolist()
columns_datasets = set([column.split(".")[0] for column in columns])
column_combinations = combinations(columns_datasets, 2)
# train: 47 x 8 -> x = 1 x 8, y = 46 x 8
# test: 47 x 8 -> x = 1 x 8, y = 46 x 8

# For each column in the DataFrame
for col in column_combinations:
    # Use the column as the input and the remaining columns as the target
    columns = [column for column in df.columns if any(item in column for item in col)]
    x = X[columns]
    y = X

    # Initialize a list to store the RMSE for each target column
    rmse_scores = []

    # For each row (leave-one-out cross-validation)
    for train_index, test_index in kfold.split(x):
        model = LinearRegression()
        # Split the data into training and testing sets
        x_train, x_test = x.iloc[train_index], x.iloc[test_index]
        y_train, y_test = y.iloc[train_index], y.iloc[test_index]

        # Fit the model
        model.fit(x_train, y_train)

        # Make predictions
        y_pred = model.predict(x_test)

        # Calculate the RMSE and add it to the list
        rmse_scores.append(root_mean_squared_error(y_test, y_pred))

    # Calculate the average RMSE
    avg_rmse = np.mean(rmse_scores)
    std_rmse = np.std(rmse_scores)

    # Store the average RMSE in the dictionary
    avg_rmse_dict[col] = avg_rmse
    std_rmse_dict[col] = std_rmse

# Find the metric with the lowest RMSE
best_metric = min(avg_rmse_dict, key=avg_rmse_dict.get)

print(
    f"The most predictive metric is {best_metric} with an average RMSE of {avg_rmse_dict[best_metric]}"
)
# print(f'-- Mean RMSE --')
# print(avg_rmse_dict)
# print(f'-- Std RMSE --')
# print(std_rmse_dict)

# sort by value
sorted_avg_rmse_dict = sorted(avg_rmse_dict.items(), key=lambda x: x[1])
sorted_std_rmse_dict = sorted(std_rmse_dict.items(), key=lambda x: x[1])

print(f"-- Mean RMSE Sorted --")
print(sorted_avg_rmse_dict)
print(f"-- Std RMSE Sorted --")
print(sorted_std_rmse_dict)

The most predictive metric is ('diabetic', 'kinetics') with an average RMSE of 2.0248366128708963

-- Mean RMSE Sorted --

[
    (('diabetic', 'kinetics'), 2.0248366128708963),
    (('imagenet1k', 'ucf'), 2.0365935760303713),
    (('hmdb51', 'food101'), 2.065328421341288),
    (('places365', 'ucf'), 2.0846660931170238),
    (('diabetic', 'ucf'), 2.0873301600492877),
    (('imagenet1k', 'kinetics'), 2.0997945333299493),
    (('hmdb51', 'imagenet1k'), 2.1458637573974224),
    (('hmdb51', 'diabetic'), 2.146763890459965),
    (('clevr', 'imagenet1k'), 2.1798408940978438),
    (('places365', 'hmdb51'), 2.216916836224894),
    (('food101', 'ucf'), 2.228543173394324),
    (('dtextures', 'imagenet1k'), 2.231550452077762),
    (('places365', 'kinetics'), 2.2375913694324012),
    (('food101', 'kinetics'), 2.290552535369977),
    (('cifar100', 'imagenet1k'), 2.306683916537244),
    (('ade20k', 'food101'), 2.311840097030975),
    (('dtextures', 'places365'), 2.3593470606660096),
    (('mini', 'food101'), 2.388771428901172),
    (('dtextures', 'food101'), 2.414496054839252),
    (('chexpert', 'kinetics'), 2.419001638964245),
    (('kinetics', 'fungi'), 2.446178668311514),
    (('clevr-math', 'food101'), 2.451090257123052),
    (('iwildcam', 'food101'), 2.459639048801557),
    (('dtextures', 'diabetic'), 2.463655704438607),
    (('chexpert', 'food101'), 2.499503722809614),
    (('cifar100', 'diabetic'), 2.5052955043775667),
    (('clevr-math', 'imagenet1k'), 2.5232005516758305),
    (('cifar100', 'kinetics'), 2.526451284140843),
    (('vgg', 'food101'), 2.531742543162732),
    (('hmdb51', 'fungi'), 2.556239303918993),
    (('clevr', 'food101'), 2.5627976414783964),
    (('omniglot', 'food101'), 2.566709521653496),
    (('chexpert', 'hmdb51'), 2.5776203305769387),
    (('food101', 'diabetic'), 2.584513917190975),
    (('fungi', 'ucf'), 2.589196159555628),
    (('chexpert', 'ucf'), 2.590767182414157),
    (('vgg', 'imagenet1k'), 2.593840472159187),
    (('food101', 'acdc'), 2.62716029698417),
    (('food101', 'winoground'), 2.6352331944536886),
    (('clevr-math', 'diabetic'), 2.6709515533733064),
    (('kinetics', 'ucf'), 2.6784316867629605),
    (('cifar100', 'ucf'), 2.6796181805636863),
    (('food101', 'imagenet1k'), 2.690208431024263),
    (('nyu', 'food101'), 2.702979019618795),
    (('cifar100', 'hmdb51'), 2.7062632472986943),
    (('newyorkercaptioncontest', 'kinetics'), 2.7251290153297067),
    (('mini', 'imagenet1k'), 2.7260428909710877),
    (('newyorkercaptioncontest', 'imagenet1k'), 2.728656808978136),
    (('vgg', 'kinetics'), 2.7336836886814115),
    (('dtextures', 'kinetics'), 2.745695466617485),
    (('cifar100', 'chexpert'), 2.7538544791264075),
    (('cubirds', 'kinetics'), 2.7721970867452455),
    (('dtextures', 'chexpert'), 2.7722210270992025),
    (('ade20k', 'imagenet1k'), 2.7766494101722845),
    (('food101', 'fungi'), 2.7825936501067634),
    (('pascal', 'ucf'), 2.8074383589760714),
    (('cifar100', 'cubirds'), 2.8160456263287594),
    (('cubirds', 'ucf'), 2.8171013501921163),
    (('vgg', 'ucf'), 2.8194547575186926),
    (('cubirds', 'hmdb51'), 2.836603244885727),
    (('imagenet1k', 'flickr30k'), 2.849262090962294),
    (('pascal', 'kinetics'), 2.862417103491159),
    (('cifar100', 'vgg'), 2.863398197120028),
    (('kinetics', 'flickr30k'), 2.864213579996922),
    (('clevr', 'fungi'), 2.8680929092423066),
    (('clevr', 'diabetic'), 2.869021530583102),
    (('vgg', 'hmdb51'), 2.882312041516762),
    (('newyorkercaptioncontest', 'hmdb51'), 2.886442918178096),
    (('newyorkercaptioncontest', 'ucf'), 2.890851725960267),
    (('clevr', 'places365'), 2.8951935226658616),
    (('cubirds', 'food101'), 2.8955235569715496),
    (('hmdb51', 'flickr30k'), 2.895726581179394),
    (('pascal', 'diabetic'), 2.9023407857905963),
    (('mini', 'diabetic'), 2.905182660014824),
    (('pascal', 'imagenet1k'), 2.9071689801147333),
    (('pascal', 'food101'), 2.9203317249563145),
    (('ade20k', 'diabetic'), 2.922850511839521),
    (('newyorkercaptioncontest', 'ham10k'), 2.930495878135287),
    (('cifar100', 'omniglot'), 2.9604918732064087),
    (('cifar10

-- Std RMSE Sorted --

[
    (('ade20k', 'acdc'), 0.7843029649211404),
    (('cifar100', 'winoground'), 0.7871183736494359),
    (('omniglot', 'ade20k'), 0.8273670940252079),
    (('ade20k', 'cubirds'), 0.8557480358344508),
    (('ade20k', 'imagenet1k'), 0.8678806662010035),
    (('cifar100', 'acdc'), 0.9259566035397),
    (('dtextures', 'acdc'), 0.9315680334069292),
    (('imagenet1k', 'flickr30k'), 0.979643345737897),
    (('diabetic', 'flickr30k'), 0.9911712341040573),
    (('acdc', 'ucf'), 0.9955991914228963),
    (('kinetics', 'ucf'), 0.9997856044279282),
    (('cifar100', 'nyu'), 1.0041055467215458),
    (('cifar100', 'diabetic'), 1.0097729522251968),
    (('dtextures', 'diabetic'), 1.0117558933208755),
    (('vgg', 'nyu'), 1.0358075305575822),
    (('dtextures', 'imagenet1k'), 1.0389208027117818),
    (('cifar100', 'imagenet1k'), 1.039817849930129),
    (('hmdb51', 'food101'), 1.0452492212745603),
    (('cifar100', 'cubirds'), 1.047499213146933),
    (('hmdb51', 'flickr30k'), 1.0485858328378064),
    (('newyorkercaptioncontest', 'nyu'), 1.0486286431926424),
    (('ade20k', 'hmdb51'), 1.04958514173372),
    (('ade20k', 'fungi'), 1.0618715521343463),
    (('food101', 'winoground'), 1.0642848906987934),
    (('clevr-math', 'ade20k'), 1.0690139478907672),
    (('newyorkercaptioncontest', 'winoground'), 1.081938228733491),
    (('cifar100', 'omniglot'), 1.0905378404151413),
    (('diabetic', 'kinetics'), 1.0942895578583685),
    (('kinetics', 'acdc'), 1.0957813089383415),
    (('nyu', 'flickr30k'), 1.0964146626345475),
    (('kinetics', 'fungi'), 1.1013488219356897),
    (('chexpert', 'nyu'), 1.1017608713444214),
    (('cifar100', 'ade20k'), 1.1093533733197078),
    (('mini', 'imagenet1k'), 1.1183586303261654),
    (('clevr-math', 'pascal'), 1.1186416439742197),
    (('dtextures', 'chexpert'), 1.1192942938273176),
    (('dtextures', 'kinetics'), 1.1242025014286647),
    (('dtextures', 'flickr30k'), 1.12771785163092),
    (('ade20k', 'iwildcam'), 1.1313699735936664),
    (('dtextures', 'places365'), 1.131524871734451),
    (('kinetics', 'flickr30k'), 1.1321982629182),
    (('vgg', 'ade20k'), 1.1382129788136306),
    (('imagenet1k', 'kinetics'), 1.145843419191926),
    (('ade20k', 'diabetic'), 1.1472633281556068),
    (('clevr-math', 'acdc'), 1.1491486166524132),
    (('newyorkercaptioncontest', 'chexpert'), 1.1502770598573793),
    (('newyorkercaptioncontest', 'ham10k'), 1.1541092364370489),
    (('newyorkercaptioncontest', 'kinetics'), 1.1566753506328145),
    (('vgg', 'imagenet1k'), 1.1587048764871475),
    (('cifar100', 'ham10k'), 1.1592529546861838),
    (('pascal', 'imagenet1k'), 1.1690776644831393),
    (('hmdb51', 'diabetic'), 1.170865426520504),
    (('nyu', 'fungi'), 1.171435953505947),
    (('hmdb51', 'acdc'), 1.1736666527797643),
    (('omniglot', 'food101'), 1.1806637261929815),
    (('cifar100', 'iwildcam'), 1.1873272756052793),
    (('newyorkercaptioncontest', 'imagenet1k'), 1.1922976525510904),
    (('newyorkercaptioncontest', 'hmdb51'), 1.1926146364596562),
    (('chexpert', 'food101'), 1.1938061093267094),
    (('iwildcam', 'food101'), 1.1972585426619748),
    (('omniglot', 'iwildcam'), 1.203250687404666),
    (('diabetic', 'ucf'), 1.2034881618884656),
    (('iwildcam', 'fungi'), 1.2072380856294196),
    (('ade20k', 'ucf'), 1.2112805837085894),
    (('clevr-math', 'cifar100'), 1.2138067459111845),
    (('food101', 'acdc'), 1.2235970433631076),
    (('hmdb51', 'imagenet1k'), 1.2254928330165173),
    (('dtextures', 'cubirds'), 1.229475489611009),
    (('cifar100', 'vgg'), 1.2414096354747086),
    (('pascal', 'ucf'), 1.2417369974272474),
    (('cifar100', 'fungi'), 1.2481777454513312),
    (('cifar100', 'chexpert'), 1.251205999340059),
    (('ade20k', 'food101'), 1.2522020764516117),
    (('cifar100', 'hmdb51'), 1.2544888702967598),
    (('cifar100', 'kinetics'), 1.260662844046189),
    (('dtextures', 'pascal'), 1.2621402450112726),
    (('pascal', 'winoground'), 1.2671587532025268),
    (('fungi', 'ucf'), 1.2695387719330786),
    (('

In [9]:
from itertools import combinations
from sklearn.linear_model import LinearRegression
from sklearn.model_selection import KFold
from sklearn.metrics import root_mean_squared_error

# Assuming df is your DataFrame
X = df.copy()
X.dropna(inplace=True)
# Create a linear regression model


# Use leave-one-out cross-validation
kfold = KFold(n_splits=10)

# Dictionary to store the average RMSE for each metric
avg_rmse_dict = {}
std_rmse_dict = {}
# 47 x 16
column_pairs = []

columns = df.columns.tolist()
columns_datasets = set([column.split(".")[0] for column in columns])
column_combinations = combinations(columns_datasets, 3)
# train: 47 x 8 -> x = 1 x 8, y = 46 x 8
# test: 47 x 8 -> x = 1 x 8, y = 46 x 8

# For each column in the DataFrame
for col in column_combinations:
    # Use the column as the input and the remaining columns as the target
    columns = [column for column in df.columns if any(item in column for item in col)]
    x = X[columns]
    y = X

    # Initialize a list to store the RMSE for each target column
    rmse_scores = []

    # For each row (leave-one-out cross-validation)
    for train_index, test_index in kfold.split(x):
        model = LinearRegression()
        # Split the data into training and testing sets
        x_train, x_test = x.iloc[train_index], x.iloc[test_index]
        y_train, y_test = y.iloc[train_index], y.iloc[test_index]

        # Fit the model
        model.fit(x_train, y_train)

        # Make predictions
        y_pred = model.predict(x_test)

        # Calculate the RMSE and add it to the list
        rmse_scores.append(root_mean_squared_error(y_test, y_pred))

    # Calculate the average RMSE
    avg_rmse = np.mean(rmse_scores)
    std_rmse = np.std(rmse_scores)

    # Store the average RMSE in the dictionary
    avg_rmse_dict[col] = avg_rmse
    std_rmse_dict[col] = std_rmse

# Find the metric with the lowest RMSE
best_metric = min(avg_rmse_dict, key=avg_rmse_dict.get)

print(
    f"The most predictive metric is {best_metric} with an average RMSE of {avg_rmse_dict[best_metric]}"
)
# print(f'-- Mean RMSE --')
# print(avg_rmse_dict)
# print(f'-- Std RMSE --')
# print(std_rmse_dict)

# sort by value
sorted_avg_rmse_dict = sorted(avg_rmse_dict.items(), key=lambda x: x[1])
sorted_std_rmse_dict = sorted(std_rmse_dict.items(), key=lambda x: x[1])

print(f"-- Mean RMSE Sorted --")
print(sorted_avg_rmse_dict)
print(f"-- Std RMSE Sorted --")
print(sorted_std_rmse_dict)

The most predictive metric is ('clevr-math', 'imagenet1k', 'kinetics') with an average RMSE of 1.6611391782920937

-- Mean RMSE Sorted --

[
    (('clevr-math', 'imagenet1k', 'kinetics'), 1.6611391782920937),
    (('imagenet1k', 'kinetics', 'ucf'), 1.6793958926020836),
    (('clevr', 'imagenet1k', 'kinetics'), 1.6808277648058265),
    (('dtextures', 'imagenet1k', 'ham10k'), 1.7406521917004842),
    (('dtextures', 'imagenet1k', 'kinetics'), 1.7654720772212158),
    (('imagenet1k', 'kinetics', 'ham10k'), 1.77102264784133),
    (('hmdb51', 'imagenet1k', 'ham10k'), 1.7829942492044968),
    (('clevr-math', 'hmdb51', 'imagenet1k'), 1.820083675804965),
    (('places365', 'hmdb51', 'ucf'), 1.824264191603445),
    (('cifar100', 'hmdb51', 'imagenet1k'), 1.841404645181671),
    (('dtextures', 'clevr', 'imagenet1k'), 1.8429047116842532),
    (('hmdb51', 'imagenet1k', 'kinetics'), 1.8446564767539155),
    (('imagenet1k', 'ham10k', 'ucf'), 1.84586761664723),
    (('ade20k', 'imagenet1k', 'ucf'), 1.8554963009452972),
    (('hmdb51', 'imagenet1k', 'ucf'), 1.856693442000946),
    (('diabetic', 'imagenet1k', 'ucf'), 1.8652583536877358),
    (('cifar100', 'imagenet1k', 'kinetics'), 1.9135099369334256),
    (('clevr', 'imagenet1k', 'ucf'), 1.9135625445716709),
    (('cifar100', 'places365', 'hmdb51'), 1.9135779017395755),
    (('imagenet1k', 'winoground', 'kinetics'), 1.9286395989428144),
    (('cifar100', 'imagenet1k', 'ucf'), 1.9493106626598014),
    (('diabetic', 'kinetics', 'ucf'), 1.9603669003986988),
    (('clevr', 'hmdb51', 'imagenet1k'), 1.969374828985688),
    (('vgg', 'imagenet1k', 'kinetics'), 1.9788973966725192),
    (('ade20k', 'imagenet1k', 'kinetics'), 1.994044802883933),
    (('imagenet1k', 'winoground', 'ucf'), 1.996305175410641),
    (('clevr-math', 'imagenet1k', 'ucf'), 2.0108209291709143),
    (('vgg', 'imagenet1k', 'ucf'), 2.012425457439786),
    (('mini', 'places365', 'hmdb51'), 2.0130054287197154),
    (('mini', 'places365', 'ucf'), 2.0160404467556994),
    (('hmdb51', 'diabetic', 'imagenet1k'), 2.0251802978477764),
    (('hmdb51', 'imagenet1k', 'winoground'), 2.034826044251585),
    (('places365', 'hmdb51', 'kinetics'), 2.0350856920311053),
    (('omniglot', 'imagenet1k', 'kinetics'), 2.0498187143272966),
    (('chexpert', 'kinetics', 'ucf'), 2.051600671322258),
    (('mini', 'diabetic', 'kinetics'), 2.051992148890156),
    (('dtextures', 'omniglot', 'imagenet1k'), 2.056437336552068),
    (('diabetic', 'imagenet1k', 'kinetics'), 2.056709931885951),
    (('cifar100', 'places365', 'ucf'), 2.0623250072953927),
    (('mini', 'hmdb51', 'food101'), 2.062859163170289),
    (('mini', 'diabetic', 'ucf'), 2.0682356104583755),
    (('clevr-math', 'dtextures', 'imagenet1k'), 2.0699084750905774),
    (('chexpert', 'diabetic', 'ucf'), 2.070209242398523),
    (('dtextures', 'imagenet1k', 'ucf'), 2.084486673271477),
    (('places365', 'kinetics', 'ucf'), 2.08662979427805),
    (('mini', 'hmdb51', 'imagenet1k'), 2.0892737929563174),
    (('nyu', 'imagenet1k', 'ucf'), 2.103265274747689),
    (('cifar100', 'vgg', 'hmdb51'), 2.1066643361709425),
    (('places365', 'winoground', 'ucf'), 2.1073535925670477),
    (('omniglot', 'imagenet1k', 'ucf'), 2.113242847061705),
    (('iwildcam', 'diabetic', 'kinetics'), 2.113250374852224),
    (('chexpert', 'diabetic', 'kinetics'), 2.1146179092323267),
    (('mini', 'food101', 'kinetics'), 2.1204701295048722),
    (('dtextures', 'mini', 'imagenet1k'), 2.1225368539100478),
    (('dtextures', 'diabetic', 'kinetics'), 2.127156255271121),
    (('clevr', 'diabetic', 'ucf'), 2.128422113364201),
    (('vgg', 'clevr', 'imagenet1k'), 2.1287545443733715),
    (('places365', 'kinetics', 'ham10k'), 2.1289273447083237),
    (('cubirds', 'imagenet1k', 'kinetics'), 2.1426236037537185),
    (('places365', 'diabetic', 'ucf'), 2.1427618306923732),
    (('omniglot', 'diabetic', 'ucf'), 2.1441836417678366),
    (('cifar100', 'dtextures', 'imagenet1k'), 2.150468944072461),
    (('hmdb51', 'diabetic', 'kinetics'), 2.150880834383911),
    (('diabetic', 'kinetics', 'ham10k'), 2.151072934116946),
    (('clevr-math', 'hmdb51', 'food101'), 2.1532527163384456),
    (('

-- Std RMSE Sorted --

[
    (('ade20k', 'cubirds', 'acdc'), 0.5907415428523326),
    (('omniglot', 'ade20k', 'acdc'), 0.5955086810030563),
    (('dtextures', 'imagenet1k', 'ham10k'), 0.6472114584307018),
    (('omniglot', 'imagenet1k', 'flickr30k'), 0.6771195032619036),
    (('ade20k', 'iwildcam', 'acdc'), 0.7068079273857537),
    (('clevr-math', 'pascal', 'mini'), 0.731767570124379),
    (('vgg', 'omniglot', 'imagenet1k'), 0.7394134746100944),
    (('omniglot', 'ade20k', 'cubirds'), 0.7596753942175936),
    (('omniglot', 'ade20k', 'diabetic'), 0.774615106849707),
    (('ade20k', 'imagenet1k', 'fungi'), 0.7829742313072262),
    (('vgg', 'cubirds', 'imagenet1k'), 0.7832381924926387),
    (('dtextures', 'nyu', 'kinetics'), 0.7850225466612956),
    (('dtextures', 'omniglot', 'iwildcam'), 0.7901537328882955),
    (('vgg', 'kinetics', 'ucf'), 0.791112287896117),
    (('vgg', 'chexpert', 'nyu'), 0.7930725438569888),
    (('cifar100', 'hmdb51', 'nyu'), 0.7938432119108715),
    (('vgg', 'nyu', 'acdc'), 0.7971989474763558),
    (('kinetics', 'acdc', 'ucf'), 0.800093026736136),
    (('dtextures', 'ade20k', 'acdc'), 0.8011593393288902),
    (('dtextures', 'nyu', 'diabetic'), 0.8033191172298667),
    (('cifar100', 'chexpert', 'imagenet1k'), 0.8035439440166247),
    (('ade20k', 'hmdb51', 'acdc'), 0.8035829580766259),
    (('cifar100', 'winoground', 'acdc'), 0.8037943785564285),
    (('vgg', 'nyu', 'kinetics'), 0.8045307083773121),
    (('cubirds', 'imagenet1k', 'flickr30k'), 0.808672005951533),
    (('omniglot', 'ade20k', 'iwildcam'), 0.8092821305663181),
    (('dtextures', 'pascal', 'nyu'), 0.8141792983734224),
    (('vgg', 'imagenet1k', 'winoground'), 0.817602864603249),
    (('ade20k', 'imagenet1k', 'acdc'), 0.8187912271067185),
    (('ade20k', 'iwildcam', 'fungi'), 0.8189164148564214),
    (('dtextures', 'chexpert', 'nyu'), 0.8245531167870835),
    (('hmdb51', 'acdc', 'flickr30k'), 0.8262029687559467),
    (('cifar100', 'cubirds', 'winoground'), 0.8273099101447822),
    (('ade20k', 'acdc', 'fungi'), 0.8308653762424679),
    (('vgg', 'imagenet1k', 'kinetics'), 0.8326543855498942),
    (('dtextures', 'kinetics', 'acdc'), 0.8332012238027344),
    (('nyu', 'diabetic', 'kinetics'), 0.8388656375137148),
    (('cifar100', 'hmdb51', 'imagenet1k'), 0.8415605980304541),
    (('omniglot', 'pascal', 'winoground'), 0.8438333628573678),
    (('dtextures', 'ade20k', 'chexpert'), 0.8443511777325128),
    (('cifar100', 'dtextures', 'vgg'), 0.8444898555445538),
    (('vgg', 'imagenet1k', 'flickr30k'), 0.8514108085878243),
    (('iwildcam', 'chexpert', 'nyu'), 0.8541000771467046),
    (('dtextures', 'ade20k', 'diabetic'), 0.855828426160537),
    (('vgg', 'ade20k', 'diabetic'), 0.8560317603073397),
    (('imagenet1k', 'winoground', 'kinetics'), 0.8565028301949352),
    (('newyorkercaptioncontest', 'nyu', 'winoground'), 0.8578254040383517),
    (('dtextures', 'ade20k', 'cubirds'), 0.8692100963904889),
    (('cifar100', 'omniglot', 'winoground'), 0.8721084737092305),
    (('newyorkercaptioncontest', 'imagenet1k', 'winoground'), 0.8726192513095933),
    (('omniglot', 'iwildcam', 'ham10k'), 0.8733144208336304),
    (('clevr-math', 'ade20k', 'acdc'), 0.8734177454905678),
    (('ade20k', 'diabetic', 'imagenet1k'), 0.8734973623295306),
    (('iwildcam', 'cubirds', 'nyu'), 0.873813791485268),
    (('dtextures', 'omniglot', 'imagenet1k'), 0.8807400557202535),
    (('imagenet1k', 'kinetics', 'ham10k'), 0.8830557616721614),
    (('dtextures', 'omniglot', 'pascal'), 0.8831002078278429),
    (('cifar100', 'vgg', 'hmdb51'), 0.8851895522440737),
    (('dtextures', 'nyu', 'acdc'), 0.886230167138087),
    (('vgg', 'ade20k', 'acdc'), 0.889544878889369),
    (('vgg', 'omniglot', 'nyu'), 0.8903491249453263),
    (('pascal', 'imagenet1k', 'flickr30k'), 0.8939913009605283),
    (('hmdb51', 'imagenet1k', 'ham10k'), 0.8954583027114256),
    (('dtextures', 'cubirds', 'imagenet1k'), 0.8960667184066512),
    (('vgg', 'kinetics', 'ham10k'), 0.8965740044598384),
    (('hmdb51', 'imagenet1k', 'kinetics'), 